## Eval Script

In [1]:
import sys
import re
from copy import copy
from collections import defaultdict
from optparse import OptionParser

# try:
#     f = open("/Users/anthonymunoz/ISTDTerm6/MachineLearning/ML NLP Project/EvalScript/dev.out",encoding = 'utf-8')
#     data = f.readlines()
# finally:
#     f.close()

# print(data)
# print(len(data))
# print(data[:10])

#Read entities from predcition
def get_predicted(predicted, answers=defaultdict(lambda: defaultdict(defaultdict))):

    example = 0
    word_index = 0
    entity = []
    last_ne = "O"
    last_sent = ""
    last_entity = []

    answers[example] = []
    for line in predicted:
        line = line.strip()
#         print(line)
        if line.startswith("##"):
            continue
        elif len(line) == 0:
            if entity:
                answers[example].append(list(entity))
                entity = []

            example += 1
            answers[example] = []
            word_index = 0
            last_ne = "O"
            continue
        else:
            split_line = line.split(separator)
            #word = split_line[0]
            value = split_line[outputColumnIndex]
            ne = value[0]
            sent = value[2:]


            last_entity = []

            #check if it is start of entity
            if ne == 'B' or (ne == 'I' and last_ne == 'O') or (last_ne != 'O' and ne == 'I' and last_sent != sent):
                if entity:
                    last_entity = list(entity)

                entity = [sent]
                    
                entity.append(word_index)

            elif ne == 'I':
                entity.append(word_index)

            elif ne == 'O':
                if last_ne == 'B' or last_ne == 'I':
                    last_entity =list(entity)
                entity = []


            if last_entity:
                answers[example].append(list(last_entity))
                last_entity = []

        last_sent = sent
        last_ne = ne
        word_index += 1

    if entity:
        answers[example].append(list(entity))


    return answers



#Read entities from gold data
def get_observed(observed):


    example = 0
    word_index = 0
    entity = []
    last_ne = "O"
    last_sent = ""
    last_entity = []

    observations=defaultdict(defaultdict)
    observations[example] = []

    for line in observed:
        line = line.strip()
#         print(line)
        if line.startswith("##"):
            continue
        elif len(line) == 0:
            if entity:
                observations[example].append(list(entity))
                entity = []

            example += 1
            observations[example] = []
            word_index = 0
            last_ne = "O"
            continue

        else:
            split_line = line.split(separator)
            word = split_line[0]
            value = split_line[outputColumnIndex]
            ne = value[0]
            sent = value[2:]


            last_entity = []

            #check if it is start of entity, suppose there is no weird case in gold data
            if ne == 'B' or (ne == 'I' and last_ne == 'O') or (last_ne != 'O' and ne == 'I' and last_sent != sent):
                if entity:
                    last_entity = entity

                entity = [sent]
                    
                entity.append(word_index)

            elif ne == 'I':
                entity.append(word_index)

            elif ne == 'O':
                if last_ne == 'B' or last_ne == 'I':
                    last_entity = entity
                entity = []


            if last_entity:
                observations[example].append(list(last_entity))
                last_entity = []


        last_ne = ne
        last_sent = sent
        word_index += 1

    if entity:
        observations[example].append(list(entity))

    return observations

#Print Results and deal with division by 0
def printResult(evalTarget, num_correct, prec, rec):
    if abs(prec + rec ) < 1e-6:
        f = 0
    else:
        f = 2 * prec * rec / (prec + rec)
    print('#Correct', evalTarget, ':', num_correct)
    print(evalTarget, ' precision: %.4f' % (prec))
    print(evalTarget, ' recall: %.4f' %   (rec))
    print(evalTarget, ' F: %.4f' % (f))

#Compare results bewteen gold data and prediction data
def compare_observed_to_predicted(observed, predicted):

    correct_sentiment = 0
    correct_entity = 0

    total_observed = 0.0
    total_predicted = 0.0

    #For each Instance Index example (example = 0,1,2,3.....)
    for example in observed:
        observed_instance = observed[example]
        predicted_instance = predicted[example]

        #Count number of entities in gold data
        total_observed += len(observed_instance)
        #Count number of entities in prediction data
        total_predicted += len(predicted_instance)

        #For each entity in prediction
        for span in predicted_instance:
            span_begin = span[1]
            span_length = len(span) - 1
            span_ne = (span_begin, span_length)
            span_sent = span[0]

            #For each entity in gold data
            for observed_span in observed_instance:
                begin = observed_span[1]
                length = len(observed_span) - 1
                ne = (begin, length)
                sent = observed_span[0]

                #Entity matched
                if span_ne == ne:
                    correct_entity += 1
                    

                    #Entity & Sentiment both are matched
                    if span_sent == sent:
                        correct_sentiment += 1

    print()
    print('#Entity in gold data: %d' % (total_observed))
    print('#Entity in prediction: %d' % (total_predicted))
    print()

    prec = correct_entity/total_predicted
    rec = correct_entity/total_observed
    printResult('Entity', correct_entity, prec, rec)
    print()

    prec = correct_sentiment/total_predicted
    rec = correct_sentiment/total_observed
    printResult('Sentiment',correct_sentiment, prec, rec)


In [2]:
import pandas as pd
import numpy as np
import math
from tqdm import tqdm

### Loading the dataset

In [3]:

def get_word_and_tag(path):
    try:
        words = []
        tags = []
        word_tag = []
        f = open(path + '/train',encoding = 'utf-8')
        data = f.readlines()
        for x in data:
            if len(x)<2:
#                 print(x)
                continue
            line = x.rstrip()
            temp = line.split(' ')
            word_tag.append(temp)
            words.append(temp[0])
            tags.append(temp[1])
        return words,tags,word_tag
    finally:
        f.close()
        
en_word ,en_tags, en_word_tag = get_word_and_tag('EN')
# print(en_word_tag[:30])
# print(en_tags[:30])
# print(len(en_word_tag))
# print(en_word_tag[:30])

def get_dictionaries(word_tag):
    label_count = dict()
    for i in word_tag:
        label_count[i[1]] = label_count.get(i[1], 0) + 1
        
#     print(label_count)
    
    word_count = dict()
    for i in word_tag:
        word_count[i[0]] = word_count.get(i[0], 0) + 1
        
#     print(word_count)
    
    y_to_x = dict()
    for i in word_tag:
        y_to_x[i[0]+i[1]] = y_to_x.get(i[0]+i[1], 0) + 1
        
#     print(y_to_x)
                  
    return label_count,word_count,y_to_x
        
en_label_count, en_word_count , en_y_to_x = get_dictionaries(en_word_tag)
# print(en_label_count)
# print(en_word_count)
print(en_y_to_x)

{'MunicipalB-NP': 1, 'bondsI-NP': 99, 'areB-VP': 677, 'generallyB-ADVP': 12, 'aB-ADJP': 3, 'bitI-ADJP': 2, 'saferI-ADJP': 1, 'thanB-PP': 128, 'corporateB-NP': 28, 'inB-PP': 2862, 'aB-NP': 3589, 'recessionI-NP': 35, ',O': 8705, 'butO': 292, 'notB-ADJP': 6, 'asI-ADJP': 7, 'safeI-ADJP': 2, 'asB-PP': 364, 'bondsB-NP': 21, 'issuedB-VP': 14, 'byB-PP': 868, 'theB-NP': 7756, 'federalI-NP': 61, 'governmentI-NP': 122, '.O': 7449, 'HeB-NP': 153, 'addedB-VP': 64, 'thatB-SBAR': 793, 'costI-NP': 38, 'forB-PP': 1504, 'stress-relatedB-NP': 5, 'compensationI-NP': 3, 'claimsI-NP': 23, 'isB-VP': 1190, 'aboutB-NP': 203, 'twiceI-NP': 2, 'theI-NP': 74, 'averageI-NP': 43, 'allB-NP': 152, 'injuryI-NP': 1, 'TheB-NP': 1255, 'incidentI-NP': 4, 'occurredB-VP': 6, 'SaturdayB-NP': 6, 'nightI-NP': 27, 'saidB-VP': 1000, ':O': 276, '``O': 1089, 'WeB-NP': 110, 'knowB-VP': 17, 'ofB-PP': 4304, 'noB-NP': 102, 'technologyI-NP': 17, 'thatB-NP': 676, 'existsB-VP': 3, 'anywhereB-ADVP': 1, 'worldI-NP': 31, 'wouldB-VP': 392, 'a

In [4]:
def get_emission(x,y,xy_dict,label_dict):
    if x+y not in xy_dict:
        return 0.0
    count_y_to_x = xy_dict[x+y]
    count_y = label_dict[y]
    return count_y_to_x/count_y

# print(get_emission('Municipal','B-NP',smoothed_en_y_to_x,en_label_count))
# print(smoothed_en_word_count)
# print(en_word_count)
# print(smoothed_en_word_count)

In [5]:
def smoothing(lst,word_dict,k=3):
    new_copy = np.array(lst)
    array = new_copy.copy()
    #     print(array[0])
    for tup in array:
        if word_dict[tup[0]] < k:
            tup[0] = '#UNK#'
    return array

# print(en_word_tag[:30])
print(en_word_count)
smoothed_en_word_tag = smoothing(en_word_tag,en_word_count)
print(smoothed_en_word_tag)


{'Municipal': 2, 'bonds': 120, 'are': 681, 'generally': 18, 'a': 3695, 'bit': 13, 'safer': 1, 'than': 304, 'corporate': 49, 'in': 2926, 'recession': 37, ',': 9207, 'but': 325, 'not': 218, 'as': 781, 'safe': 12, 'issued': 22, 'by': 870, 'the': 7862, 'federal': 100, 'government': 146, '.': 7463, 'He': 153, 'added': 81, 'that': 1550, 'cost': 71, 'for': 1556, 'stress-related': 6, 'compensation': 4, 'claims': 35, 'is': 1201, 'about': 389, 'twice': 11, 'average': 60, 'all': 205, 'injury': 1, 'The': 1260, 'incident': 4, 'occurred': 6, 'Saturday': 9, 'night': 30, 'said': 1014, ':': 276, '``': 1270, 'We': 110, 'know': 47, 'of': 4409, 'no': 119, 'technology': 24, 'exists': 3, 'anywhere': 1, 'world': 40, 'would': 398, 'allow': 20, 'us': 35, 'to': 4425, "''": 1244, 'reinforce': 2, 'columns': 4, 'Walter': 11, 'H.': 10, 'Monteith': 1, 'Jr.': 12, 'SNET': 2, 'chairman': 93, 'and': 3109, 'chief': 106, 'executive': 95, 'officer': 59, 'Innovative': 1, 'marketing': 24, 'our': 50, 'products': 98, 'services

[['#UNK#' 'B-NP']
 ['bonds' 'I-NP']
 ['are' 'B-VP']
 ...
 ['the' 'B-NP']
 ['West' 'I-NP']
 ['...' 'O']]


### After smoothing

In [6]:

smoothed_en_label_count, smoothed_en_word_count , smoothed_en_y_to_x = get_dictionaries(smoothed_en_word_tag)
# print(smoothed_en_word_count)
# print(smoothed_en[:30])
# print(get_emission('Municipal','B-NP',smoothed_en_y_to_x,smoothed_en_label_count))
print(get_emission('are','B-VP',smoothed_en_y_to_x,en_label_count))

0.03707354471277586


In [7]:
# print(en_label_count)
# print(en_word_count)
# print(en_y_to_x)
print(smoothed_en_word_count)

{'#UNK#': 14737, 'bonds': 120, 'are': 681, 'generally': 18, 'a': 3695, 'bit': 13, 'than': 304, 'corporate': 49, 'in': 2926, 'recession': 37, ',': 9207, 'but': 325, 'not': 218, 'as': 781, 'safe': 12, 'issued': 22, 'by': 870, 'the': 7862, 'federal': 100, 'government': 146, '.': 7463, 'He': 153, 'added': 81, 'that': 1550, 'cost': 71, 'for': 1556, 'stress-related': 6, 'compensation': 4, 'claims': 35, 'is': 1201, 'about': 389, 'twice': 11, 'average': 60, 'all': 205, 'The': 1260, 'incident': 4, 'occurred': 6, 'Saturday': 9, 'night': 30, 'said': 1014, ':': 276, '``': 1270, 'We': 110, 'know': 47, 'of': 4409, 'no': 119, 'technology': 24, 'exists': 3, 'world': 40, 'would': 398, 'allow': 20, 'us': 35, 'to': 4425, "''": 1244, 'columns': 4, 'Walter': 11, 'H.': 10, 'Jr.': 12, 'chairman': 93, 'and': 3109, 'chief': 106, 'executive': 95, 'officer': 59, 'marketing': 24, 'our': 50, 'products': 98, 'services': 30, 'contributed': 19, 'increase': 97, 'revenue': 72, 'defense': 18, 'lawyers': 13, 'three': 103

In [8]:
def decode(inp,word_dict,label_dict,xy_dict,filename):
    result = []
    print(len(inp))
    orig_copy = inp.copy()
    file = open(filename,'w',encoding = 'utf-8')
    
    for word in range(len(inp)):
        if inp[word] not in word_dict:
            inp[word] = '#UNK#'

    for word in range(len(inp)):
        templist = []
        retval = []
#         print(inp[word])
        retval.append(orig_copy[word])
#         print(orig_copy[word])
        for label in list(label_dict.keys()):
#             print(templist)
            templist.append(get_emission(inp[word],label,xy_dict,label_dict))
#         print(templist)
        index = np.argmax(templist)
        retval.append(list(label_dict.keys())[index])
        result.append(retval) 
        if(orig_copy[word] == '\n' or not orig_copy[word]):
            file.write('\n')
        else:
            file.write(orig_copy[word]+' ' + list(label_dict.keys())[index]+ '\n')
#         print(result)
    file.close()
    return result

In [9]:
try:
    f = open("EN/dev.in",encoding = 'utf-8')
    dev_en = f.readlines()
finally:
    f.close()
    
for string in range(len(dev_en)):
    dev_en[string] = dev_en[string].rstrip()

# print(en_word_count)
# print(en_y_to_x)

# print(smoothed_en_label_count)
    
print(decode(dev_en,smoothed_en_word_count,smoothed_en_label_count,smoothed_en_y_to_x,'EN/p2new.dev.out'))

27225
[['HBO', 'B-NP'], ['has', 'B-VP'], ['close', 'B-ADJP'], ['to', 'B-PP'], ['24', 'I-NP'], ['million', 'I-NP'], ['subscribers', 'I-NP'], ['to', 'B-PP'], ['its', 'B-NP'], ['HBO', 'B-NP'], ['and', 'I-UCP'], ['Cinemax', 'B-INTJ'], ['networks', 'I-NP'], [',', 'O'], ['while', 'B-SBAR'], ['Showtime', 'B-NP'], ['and', 'I-UCP'], ['its', 'B-NP'], ['sister', 'B-INTJ'], ['service', 'I-NP'], [',', 'O'], ['The', 'B-NP'], ['Movie', 'B-INTJ'], ['Channel', 'B-INTJ'], [',', 'O'], ['have', 'I-VP'], ['only', 'I-CONJP'], ['about', 'B-PP'], ['10', 'I-ADVP'], ['million', 'I-NP'], [',', 'O'], ['according', 'B-PP'], ['to', 'B-PP'], ['Paul', 'B-NP'], ['Kagan', 'B-INTJ'], ['Associates', 'I-NP'], [',', 'O'], ['a', 'B-LST'], ['Carmel', 'B-INTJ'], [',', 'O'], ['Calif.', 'B-NP'], [',', 'O'], ['research', 'I-NP'], ['firm', 'I-NP'], ['.', 'O'], ['', 'B-INTJ'], ['WASHINGTON', 'B-INTJ'], ['LIES', 'B-INTJ'], ['LOW', 'B-INTJ'], ['after', 'B-SBAR'], ['the', 'B-NP'], ['stock', 'I-NP'], ['market', 'I-NP'], ["'s", 'B-NP']

In [10]:


gold = open('EN/dev.out', "r", encoding='UTF-8')
prediction = open('EN/p2new.dev.out', "r", encoding='UTF-8')

#column separator
separator = ' '

#the column index for tags
outputColumnIndex = 1
#Read Gold data
observed = get_observed(gold)

#Read Predction data
predicted = get_predicted(prediction)

#Compare
compare_observed_to_predicted(observed, predicted)


#Entity in gold data: 13179
#Entity in prediction: 19406

#Correct Entity : 9152
Entity  precision: 0.4716
Entity  recall: 0.6944
Entity  F: 0.5617

#Correct Sentiment : 7644
Sentiment  precision: 0.3939
Sentiment  recall: 0.5800
Sentiment  F: 0.4692


# AL

In [11]:
al_word ,al_tags, al_word_tag = get_word_and_tag('AL')
        
al_label_count, al_word_count , al_y_to_x = get_dictionaries(al_word_tag)

In [12]:
smoothed_al_word_tag = smoothing(al_word_tag,al_word_count)

In [13]:
smoothed_al_label_count, smoothed_al_word_count , smoothed_al_y_to_x = get_dictionaries(smoothed_al_word_tag)
# print(smoothed_al_word_count)

In [14]:
try:
    f = open("AL/dev.in",encoding = 'utf-8')
    dev_al = f.readlines()
finally:
    f.close()
    
for string in range(len(dev_al)):
    dev_al[string] = dev_al[string].rstrip()

# print(en_word_count)
# print(en_y_to_x)
    
print(decode(dev_al,smoothed_al_word_count,smoothed_al_label_count,smoothed_al_y_to_x,'AL/p2new.dev.out'))

26155
[['杭', 'B-CITY'], ['州', 'I-CITY'], ['市', 'I-CITY'], ['西', 'B-ASSIST'], ['湖', 'I-DISTRICT'], ['区', 'I-DISTRICT'], ['古', 'B-TOWN'], ['荡', 'I-TOWN'], ['新', 'B-ROAD'], ['村', 'I-COMMUNITY'], ['西', 'B-ASSIST'], ['34', 'B-FLOORNO'], ['幢', 'I-HOUSENO'], ['八', 'B-FLOORNO'], ['单', 'I-CELLNO'], ['元', 'I-CELLNO'], ['1375', 'B-ROOMNO'], ['', 'B-ROOMNO'], ['塘', 'I-COMMUNITY'], ['雅', 'B-COMMUNITY'], ['镇', 'I-TOWN'], ['顶', 'B-PERSON'], ['塘', 'I-COMMUNITY'], ['工', 'I-DEVZONE'], ['业', 'I-DEVZONE'], ['园', 'I-POI'], ['鑫', 'B-PERSON'], ['龙', 'B-DISTRICT'], ['水', 'B-COMMUNITY'], ['准', 'I-REDUNDANT'], ['仪', 'I-SUBPOI'], ['器', 'I-PERSON'], ['有', 'I-SUBPOI'], ['限', 'I-SUBPOI'], ['公', 'I-PERSON'], ['司', 'I-SUBPOI'], ['', 'B-ROOMNO'], ['中', 'B-COUNTRY'], ['国', 'I-COUNTRY'], ['浙', 'B-PROV'], ['江', 'I-PROV'], ['省', 'I-PROV'], ['温', 'B-CITY'], ['州', 'I-CITY'], ['市', 'I-CITY'], ['鹿', 'B-DISTRICT'], ['城', 'I-DISTRICT'], ['区', 'I-DISTRICT'], ['百', 'B-ROAD'], ['里', 'I-COMMUNITY'], ['东', 'B-ASSIST'], ['路', 'I-ROAD

In [15]:
gold = open('AL/dev.out', "r", encoding='UTF-8')
prediction = open('AL/p2new.dev.out', "r", encoding='UTF-8')

#column separator
separator = ' '

#the column index for tags
outputColumnIndex = 1
#Read Gold data
observed = get_observed(gold)

#Read Predction data
predicted = get_predicted(prediction)

#Compare
compare_observed_to_predicted(observed, predicted)


#Entity in gold data: 8408
#Entity in prediction: 19484

#Correct Entity : 2898
Entity  precision: 0.1487
Entity  recall: 0.3447
Entity  F: 0.2078

#Correct Sentiment : 2457
Sentiment  precision: 0.1261
Sentiment  recall: 0.2922
Sentiment  F: 0.1762


## CN

In [16]:
cn_word ,cn_tags, cn_word_tag = get_word_and_tag('CN')
        
cn_label_count, cn_word_count , cn_y_to_x = get_dictionaries(cn_word_tag)

In [17]:
smoothed_cn_word_tag = smoothing(cn_word_tag,cn_word_count)

In [18]:
smoothed_cn_label_count, smoothed_cn_word_count , smoothed_cn_y_to_x = get_dictionaries(smoothed_cn_word_tag)

In [19]:
try:
    f = open("CN/dev.in",encoding = 'utf-8')
    dev_cn = f.readlines()
finally:
    f.close()
    
for string in range(len(dev_cn)):
    dev_cn[string] = dev_cn[string].rstrip()

# print(en_word_count)
# print(en_y_to_x)
    
print(decode(dev_cn,smoothed_cn_word_count,smoothed_cn_label_count,smoothed_cn_y_to_x,'CN/p2new.dev.out'))

24225
[['一', 'I-negative'], ['觉醒', 'B-negative'], ['来天', 'B-negative'], ['都', 'O'], ['黑', 'B-neutral'], ['了', 'O'], ['。', 'O'], ['梦到', 'B-negative'], ['了', 'O'], ['继科', 'B-negative'], ['哥哥', 'I-positive'], ['，', 'O'], ['给', 'O'], ['他', 'B-negative'], ['做饭', 'B-negative'], ['忙', 'O'], ['得', 'O'], ['团团转', 'B-negative'], ['，', 'O'], ['继科', 'B-negative'], ['哥哥', 'I-positive'], ['很乖', 'B-negative'], ['，', 'O'], ['不怎么', 'B-negative'], ['爱', 'O'], ['说话', 'I-neutral'], ['。', 'O'], ['', 'B-negative'], ['#', 'B-positive'], ['向', 'O'], ['全世界', 'I-neutral'], ['吃货', 'B-positive'], ['安利', 'O'], ['#', 'B-positive'], ['哑', 'B-negative'], ['壬', 'B-negative'], ['迄', 'B-negative'], ['听到', 'O'], ['看', 'O'], ['完', 'I-negative'], ['就', 'O'], ['怀孕', 'I-positive'], ['了', 'O'], ['的', 'O'], ['演唱', 'O'], ['，', 'O'], ['就', 'O'], ['觉得', 'O'], ['心情', 'O'], ['会', 'O'], ['好', 'O'], ['很', 'O'], ['[', 'O'], ['泪', 'O'], [']', 'O'], ['[', 'O'], ['围脖', 'B-negative'], [']', 'O'], ['[', 'O'], ['手套', 'B-negative'], [']', 'O'

In [20]:
gold = open('CN/dev.out', "r", encoding='UTF-8')
prediction = open('CN/p2new.dev.out', "r", encoding='UTF-8')

#column separator
separator = ' '

#the column index for tags
outputColumnIndex = 1
#Read Gold data
observed = get_observed(gold)

#Read Predction data
predicted = get_predicted(prediction)

#Compare
compare_observed_to_predicted(observed, predicted)


#Entity in gold data: 1478
#Entity in prediction: 9373

#Correct Entity : 765
Entity  precision: 0.0816
Entity  recall: 0.5176
Entity  F: 0.1410

#Correct Sentiment : 285
Sentiment  precision: 0.0304
Sentiment  recall: 0.1928
Sentiment  F: 0.0525


## SG

In [21]:
sg_word ,sg_tags, sg_word_tag = get_word_and_tag('SG')
        
sg_label_count, sg_word_count , sg_y_to_x = get_dictionaries(sg_word_tag)

In [22]:
smoothed_sg_word_tag = smoothing(sg_word_tag,sg_word_count)

In [23]:
smoothed_sg_label_count, smoothed_sg_word_count , smoothed_sg_y_to_x = get_dictionaries(smoothed_sg_word_tag)

In [24]:
try:
    f = open("SG/dev.in",encoding = 'utf-8')
    dev_sg = f.readlines()
finally:
    f.close()
    
for string in range(len(dev_sg)):
    dev_sg[string] = dev_sg[string].rstrip()

# print(en_word_count)
# print(en_y_to_x)
    
print(decode(dev_sg,smoothed_sg_word_count,smoothed_sg_label_count,smoothed_sg_y_to_x,'SG/p2new.dev.out'))

50763
[['Tour', 'B-positive'], ['Scotland', 'B-neutral'], ['followers', 'O'], ['to', 'O'], ['visit', 'O'], ['@beley_crysta2', 'B-positive'], [',', 'I-neutral'], ['@MyExpatJob', 'B-positive'], [',', 'I-neutral'], [',', 'I-neutral'], ['@paridise15', 'B-positive'], [',', 'I-neutral'], ['@JCBlakeney76', 'B-positive'], [',', 'I-neutral'], ['@UnwearyWorld', 'B-positive'], [',', 'I-neutral'], ['@szilviade', 'B-positive'], [',', 'I-neutral'], ['@garrywatts1231', 'B-positive'], ['', 'B-positive'], ['Overwatch', 'B-positive'], [':', 'O'], ['tip', 'O'], ['!', 'O'], ['Roadhog', 'B-positive'], ['is', 'O'], ['fat', 'B-positive'], ['so', 'O'], ["he's", 'O'], ['easier', 'O'], ['to', 'O'], ['hit', 'O'], ['!', 'O'], ['Me', 'I-positive'], [':', 'O'], ['wtf', 'O'], ['blizzard', 'B-positive'], ['', 'B-positive'], ["I'm", 'O'], ['at', 'O'], ['Club', 'I-neutral'], ['Tryst', 'I-neutral'], ['in', 'O'], ['Singapore', 'B-neutral'], ['https://t.co/imMAYtNBjH', 'B-positive'], ['', 'B-positive'], ['@alexiadavis__',

In [25]:
gold = open('SG/dev.out', "r", encoding='UTF-8')
prediction = open('SG/p2new.dev.out', "r", encoding='UTF-8')

#column separator
separator = ' '

#the column index for tags
outputColumnIndex = 1
#Read Gold data
observed = get_observed(gold)

#Read Predction data
predicted = get_predicted(prediction)

#Compare
compare_observed_to_predicted(observed, predicted)


#Entity in gold data: 4537
#Entity in prediction: 18451

#Correct Entity : 2632
Entity  precision: 0.1426
Entity  recall: 0.5801
Entity  F: 0.2290

#Correct Sentiment : 1239
Sentiment  precision: 0.0672
Sentiment  recall: 0.2731
Sentiment  F: 0.1078


## Part3

In [26]:
def get_y_to_y(path):   
    try:
        f = open(path,encoding = 'utf-8')
        try_y = f.readlines()
    finally:
        f.close()
   
    sentences = []
    sentences.append('START')
    for line in try_y:
        x = line.split(' ')
    #     print(x)
        if len(x) <2:
            # linebreak
            sentences.append('STOP')
            sentences.append('START')
        else:
            sentences.append(x)
    states = []
    
    for term in range(len(sentences)-1): ## removes the last start
        if len(sentences[term])==2:
            states.append(sentences[term][1])
        else:
            states.append(sentences[term])
    for state in range(len(states)):
        states[state] = states[state].rstrip()
    return states
 

en_states = get_y_to_y("EN/train")
# print(en_states[0])
# print(smoothed_en_word_tag[:30])

def get_y_to_y_dictionary(states):
    y_to_y = dict()
    for i in range(len(states)-1):
        y_to_y[states[i]+ ' ' +states[i+1]] = y_to_y.get(states[i]+ ' '+states[i+1], 0) + 1 
        
    label_count_with_ss = dict()
    for i in range(len(states)):
        label_count_with_ss[states[i]] = label_count_with_ss.get(states[i], 0) + 1 
    return y_to_y , label_count_with_ss

en_y_to_y , en_label_count_with_ss= get_y_to_y_dictionary(en_states)
# print(en_y_to_y)
# print(smoothed_en_y_to_x)
# print(en_label_count_with_ss)


In [27]:
def get_transmission(u,v,yy_dict,label_dict):
    # u is i , v is i+1
    if u + ' ' + v not in yy_dict:
        return 0.0
    count_u_to_v = yy_dict[u + ' ' + v]
    count_y = label_dict[u]
    result = count_u_to_v/count_y
    return result

# print(en_y_to_y)
# print(en_states)
# print(en_y_to_y)
# print(en_word_tag[:30])

# get_transmission('START', 'B-NP',en_y_to_y,en_label_count_with_ss)
print(get_emission('HBO','B-NP',smoothed_en_y_to_x,en_label_count))

8.455765775288025e-05


In [28]:
# def viterbi(inp,y_to_y,y_to_x,label_dict,word_dict):
#     result = []
#     print(len(inp))
#     orig_copy = inp.copy()
# #     file = open(filename,'w',encoding = 'utf-8')
#     for sentence in range(len(sentences)):
#         for word in range(len(sentences[sentence])):
#             if sentences[sentence][word] not in word_dict:
#                 sentences[sentence][word] = '#UNK#'
# #     print(sentences[:5])


# #     for sentence in sentences:
# #         for word in range(len(sentence)):
# #             for label in list(label_dict.keys()):
                
    
#     return
    
# print(en_label_count_with_ss.keys())

In [29]:
try:
    f = open("EN/dev.in",encoding = 'utf-8')
    viterbi_en = f.readlines()
finally:
    f.close()
    
en_sentences = []
temp = []
for string in range(len(viterbi_en)):
    if viterbi_en[string] == '\n':
        en_sentences.append(temp)
        temp = []
        continue
    viterbi_en[string] = viterbi_en[string].rstrip()
    temp.append(viterbi_en[string]) 

print(en_sentences[0])

['HBO', 'has', 'close', 'to', '24', 'million', 'subscribers', 'to', 'its', 'HBO', 'and', 'Cinemax', 'networks', ',', 'while', 'Showtime', 'and', 'its', 'sister', 'service', ',', 'The', 'Movie', 'Channel', ',', 'have', 'only', 'about', '10', 'million', ',', 'according', 'to', 'Paul', 'Kagan', 'Associates', ',', 'a', 'Carmel', ',', 'Calif.', ',', 'research', 'firm', '.']


In [30]:
# viterbi(sentences,en_y_to_y,smoothed_en_y_to_x,smoothed_en_label_count,smoothed_en_word_count)

In [31]:
# def get_state_transition_matrix(y_to_y_train):
#     for label in list(y_to_y_train.keys()):
#         for label in list(y_to_y_train.keys()):
        
    
def get_emission_matrix(label_dict,word_dict,xy_dict):
    emission_matrix = []
#     print(label_dict.keys())
#     print(word_dict.keys())
    for label in list(label_dict.keys()):
#         print(label)
        emission_state = []
        for word in list(word_dict.keys()):
            emission_state.append(get_emission(word,label,xy_dict,label_dict))
        emission_matrix.append(emission_state)   
    return emission_matrix
        
# (get_emission_matrix(en_label_count,smoothed_en_word_count,smoothed_en_y_to_x))
    

In [32]:
def viterbi_sentences(sentence, word_dict,label_dict,yy_dict,yx_dict,label_dict_with_ss):
    result = []
    node_matrix = []
    backpointers = []
    calc_copy = sentence.copy()
    for word in range(len(sentence)):
         if calc_copy[word] not in word_dict:
                calc_copy[word] = '#UNK#' 
                          
#     print(calc_copy)
    
    for word in range(len(calc_copy)):
      
        if word==0:
            temp = []
            for label in list(label_dict.keys()):
#                 print(calc_copy[word])
                prev_node = 1
                emission = get_emission(calc_copy[word],label,yx_dict,label_dict)
#                 print(emission)
                transmission = get_transmission('START',label,yy_dict,label_dict_with_ss)
#                 print(transmission)

                if emission != 0:
                    emission = math.log(emission)
                else:
                    emission = -999999999
                if transmission != 0:
                    transmission = math.log(transmission)
                else:
                    transmission = -999999999

                node_value = emission+transmission





#                 node_value = prev_node*emission*transmission
                temp.append(node_value)
            node_matrix.append(temp)
            continue
            
        storage = []
        
#         if word == len(calc_copy)-1:
#             for label in list(label_dict.keys()):
#                 find_max_list = []
#                 for node in range(len(list(label_dict.keys()))): ## node in node_matrix
#         #                 print(node)
#                     prev_node = node_matrix[word-1][node]
#                     emission = get_emission(calc_copy[word],label,yx_dict,label_dict)
#         #                 print(emission)
#                     transmission = get_transmission(list(label_dict.keys())[node],label,yy_dict,label_dict_with_ss)
#         #                 print(transmission)
#                     node_value = prev_node*emission*transmission
#                     find_max_list.append(node_value)
#                 storage.append(max(find_max_list))
#             node_matrix.append(storage)
# #             print(len(node_matrix))
# #             print(node_matrix)
#             continue
        index_list = []
        for label in list(label_dict.keys()):
            find_max_list = []
            for node in range(len(list(label_dict.keys()))): ## node in node_matrix
#                 print(node)
                prev_node = node_matrix[word-1][node]
                emission = get_emission(calc_copy[word],label,yx_dict,label_dict)
#                 print(emission)
                transmission = get_transmission(list(label_dict.keys())[node],label,yy_dict,label_dict_with_ss)
#                 print(transmission)


                if emission != 0:
                    emission = math.log(emission)
                else:
                    emission = -999999999
                if transmission != 0:
                    transmission = math.log(transmission)
                else:
                    transmission = -999999999

                node_value = prev_node+emission+transmission


                
#                 node_value = prev_node*emission*transmission
                find_max_list.append(node_value)
            index = np.argmax(find_max_list)
#   
            index_list.append(index)
            
            storage.append(find_max_list[index])
#             storage.append(max(find_max_list))
        backpointers.append(index_list)
#             print(storage)
        node_matrix.append(storage)
    
    # STOP NODE
#     print(node_matrix)
    find_max_stop = []
    for node in range(len(list(label_dict.keys()))): ## node in node_matrix
#            print(node)
        prev_node = node_matrix[len(sentence)-1][node]
        transmission = get_transmission(list(label_dict.keys())[node],'STOP',yy_dict,label_dict_with_ss)
#         print(transmission)
#                 print(transmission)

        if transmission != 0:
            transmission = math.log(transmission)
        else:
            transmission = -999999999

        node_value = prev_node+transmission



#         node_value = prev_node*transmission
        find_max_stop.append(node_value)
        stop_index = np.argmax(find_max_stop)
    node_matrix.append(find_max_stop)
#     print(node_matrix)
    backpointers.append(stop_index)
#     print(len(node_matrix))
#     print(backpointers[-1])
#     print(len(sentence))
#     print(len(backpointers))
    
#     print(len(backpointers))
#     print(len(node_matrix))
#     print(node_matrix[-1])
    return node_matrix[::-1], backpointers[::-1] ## reverse to get the index


# print(len(smoothed_en_label_count))
# en_matrix , en_backpointers = viterbi_sentences(en_sentences[0],smoothed_en_word_count,smoothed_en_label_count,en_y_to_y,smoothed_en_y_to_x,en_label_count_with_ss)
# print(len(en_matrix))
# print(en_matrix)
# print(len(en_matrix))

viterbi_sentences(en_sentences[0],smoothed_en_word_count,smoothed_en_label_count,en_y_to_y,smoothed_en_y_to_x,en_label_count_with_ss)

([[-1000000260.7029076,
   -266.6071812697982,
   -1000000261.1081113,
   -1000000260.5505657,
   -1000000262.256379,
   -1000000262.4241862,
   -1000000259.5802029,
   -254.0832724209197,
   -2000000253.3478804,
   -2000000253.530475,
   -3000000247.2924585,
   -2000000257.2541726,
   -3000000247.2924585,
   -2000000256.8021874,
   -3000000247.2924585,
   -3000000247.2924585,
   -3000000247.2924585,
   -3000000247.2924585,
   -2000000265.2568617,
   -3000000247.2924585,
   -3000000247.2924585],
  [-1000000252.3364315,
   -259.46075707251043,
   -1000000251.2955884,
   -1000000253.4702587,
   -1000000254.7884367,
   -1000000256.0715568,
   -1000000251.1470982,
   -252.9384512516638,
   -1000000254.3478802,
   -2000000244.3043597,
   -2000000248.2924585,
   -1000000258.2541726,
   -2000000248.2924585,
   -1000000257.8021874,
   -2000000248.2924585,
   -2000000248.2924585,
   -2000000248.2924585,
   -2000000248.2924585,
   -1000000266.2568617,
   -2000000248.2924585,
   -2000000248.29245

In [33]:
def get_index_from_viterbi_backpointers(node_matrix,backpointers):
    ## starting from stop
#     print(backpointers)
#     print(node_matrix)
    indexes = []
    for pointer_list in range(len(backpointers)):
        if pointer_list == 0:
            indexes.append(backpointers[pointer_list])
            continue
        backtrack_index = indexes[pointer_list-1]
#         print(backtrack_index)
        
#         pointer_search = np.argmax(node_matrix[pointer_list])
#         print(node_matrix[pointer_list][pointer_search])
        indexes.append(backpointers[pointer_list][backtrack_index])
#     print(indexes)
#     print(len(indexes))
    return indexes[::-1]

        
        
        
# en_index_first_sentence = get_index_from_viterbi_backpointers(en_matrix,en_backpointers)
# # print(type(en_index_first_sentence[0]))
# answer = []
# for word in range(len(en_sentences[0])):
#     temp = []
#     temp.append(en_sentences[0][word])
# #     print(temp)
#     temp.append(list(smoothed_en_label_count.keys())[en_index_first_sentence[word]])
#     answer.append(temp)
# print(answer)
# print(smoothed_en_label_count.keys())

## Part 3

In [34]:
def decode_viterbi(sentences, word_dict,label_dict,yy_dict,yx_dict,label_dict_with_ss,filename):
#     print(sentences[0])
    results = []
    file = open(filename,'w',encoding = 'utf-8')
    for sentence in tqdm(range(len(sentences))):
        sentence_result = []
#         print(sentences[sentence])
        inverted_node_matrix , inverted_back_pointers = viterbi_sentences(sentences[sentence],word_dict,label_dict,yy_dict,yx_dict,label_dict_with_ss)
        prediction_indexes = get_index_from_viterbi_backpointers(inverted_node_matrix,inverted_back_pointers)
#         print(len(prediction_indexes))
        for word in range(len(sentences[sentence])):
            temp = []
            temp.append(sentences[sentence][word])
            temp.append(list(label_dict.keys())[prediction_indexes[word]])
            sentence_result.append(temp)
        results.append(sentence_result)
#     print(results)

    for sentence in results:
        for tup in sentence:
            file.write(tup[0]+ ' ' + tup[1]+'\n')
#             print(tup[0] + ' ' + tup[1])
#         print('/n')
        file.write('\n')
    
    file.close()
    return results



In [35]:
decode_viterbi(en_sentences,smoothed_en_word_count,smoothed_en_label_count,en_y_to_y,smoothed_en_y_to_x,en_label_count_with_ss,'EN/p3.dev.out')


100%|██████████| 1094/1094 [00:45<00:00, 23.94it/s]


[[['HBO', 'B-NP'],
  ['has', 'B-VP'],
  ['close', 'I-VP'],
  ['to', 'B-PP'],
  ['24', 'B-NP'],
  ['million', 'I-NP'],
  ['subscribers', 'I-NP'],
  ['to', 'B-PP'],
  ['its', 'B-NP'],
  ['HBO', 'I-NP'],
  ['and', 'O'],
  ['Cinemax', 'B-NP'],
  ['networks', 'I-NP'],
  [',', 'O'],
  ['while', 'B-SBAR'],
  ['Showtime', 'B-NP'],
  ['and', 'O'],
  ['its', 'B-NP'],
  ['sister', 'I-NP'],
  ['service', 'I-NP'],
  [',', 'O'],
  ['The', 'B-NP'],
  ['Movie', 'I-NP'],
  ['Channel', 'I-NP'],
  [',', 'O'],
  ['have', 'B-VP'],
  ['only', 'I-VP'],
  ['about', 'B-PP'],
  ['10', 'B-NP'],
  ['million', 'I-NP'],
  [',', 'O'],
  ['according', 'B-PP'],
  ['to', 'B-PP'],
  ['Paul', 'B-NP'],
  ['Kagan', 'I-NP'],
  ['Associates', 'I-NP'],
  [',', 'O'],
  ['a', 'B-NP'],
  ['Carmel', 'I-NP'],
  [',', 'O'],
  ['Calif.', 'B-NP'],
  [',', 'O'],
  ['research', 'B-NP'],
  ['firm', 'I-NP'],
  ['.', 'O']],
 [['WASHINGTON', 'B-NP'],
  ['LIES', 'I-NP'],
  ['LOW', 'I-NP'],
  ['after', 'B-PP'],
  ['the', 'B-NP'],
  ['stock',

In [36]:
gold = open('EN/dev.out', "r", encoding='UTF-8')
prediction = open('EN/p3.dev.out', "r", encoding='UTF-8')

#column separator
separator = ' '

#the column index for tags
outputColumnIndex = 1
#Read Gold data
observed = get_observed(gold)

#Read Predction data
predicted = get_predicted(prediction)

#Compare
compare_observed_to_predicted(observed, predicted)


#Entity in gold data: 13179
#Entity in prediction: 13055

#Correct Entity : 11089
Entity  precision: 0.8494
Entity  recall: 0.8414
Entity  F: 0.8454

#Correct Sentiment : 10668
Sentiment  precision: 0.8172
Sentiment  recall: 0.8095
Sentiment  F: 0.8133


## AL

In [37]:
al_states = get_y_to_y("AL/train")
al_y_to_y , al_label_count_with_ss= get_y_to_y_dictionary(al_states)
# print(al_y_to_y)
# print(smoothed_al_y_to_x)
# print(al_label_count_with_ss)

In [38]:
try:
    f = open("AL/dev.in",encoding = 'utf-8')
    viterbi_al = f.readlines()
finally:
    f.close()
    
al_sentences = []
temp = []
for string in range(len(viterbi_al)):
    if viterbi_al[string] == '\n':
        al_sentences.append(temp)
        temp = []
        continue
    viterbi_al[string] = viterbi_al[string].rstrip()
    temp.append(viterbi_al[string]) 
    
print(al_sentences[:2])

[['杭', '州', '市', '西', '湖', '区', '古', '荡', '新', '村', '西', '34', '幢', '八', '单', '元', '1375'], ['塘', '雅', '镇', '顶', '塘', '工', '业', '园', '鑫', '龙', '水', '准', '仪', '器', '有', '限', '公', '司']]


In [39]:
decode_viterbi(al_sentences,smoothed_al_word_count,smoothed_al_label_count,al_y_to_y,smoothed_al_y_to_x,al_label_count_with_ss,'AL/p3.dev.out')

100%|██████████| 1492/1492 [02:28<00:00, 10.05it/s]


[[['杭', 'B-CITY'],
  ['州', 'I-CITY'],
  ['市', 'I-CITY'],
  ['西', 'B-DISTRICT'],
  ['湖', 'I-DISTRICT'],
  ['区', 'I-DISTRICT'],
  ['古', 'B-TOWN'],
  ['荡', 'I-TOWN'],
  ['新', 'B-COMMUNITY'],
  ['村', 'I-COMMUNITY'],
  ['西', 'I-COMMUNITY'],
  ['34', 'B-HOUSENO'],
  ['幢', 'I-HOUSENO'],
  ['八', 'B-CELLNO'],
  ['单', 'I-CELLNO'],
  ['元', 'I-CELLNO'],
  ['1375', 'B-ROOMNO']],
 [['塘', 'B-TOWN'],
  ['雅', 'I-TOWN'],
  ['镇', 'I-TOWN'],
  ['顶', 'B-POI'],
  ['塘', 'I-POI'],
  ['工', 'I-POI'],
  ['业', 'I-POI'],
  ['园', 'I-POI'],
  ['鑫', 'I-POI'],
  ['龙', 'I-POI'],
  ['水', 'I-POI'],
  ['准', 'I-POI'],
  ['仪', 'I-POI'],
  ['器', 'I-POI'],
  ['有', 'I-POI'],
  ['限', 'I-POI'],
  ['公', 'I-POI'],
  ['司', 'I-POI']],
 [['中', 'B-COUNTRY'],
  ['国', 'I-COUNTRY'],
  ['浙', 'B-PROV'],
  ['江', 'I-PROV'],
  ['省', 'I-PROV'],
  ['温', 'B-CITY'],
  ['州', 'I-CITY'],
  ['市', 'I-CITY'],
  ['鹿', 'B-DISTRICT'],
  ['城', 'I-DISTRICT'],
  ['区', 'I-DISTRICT'],
  ['百', 'B-TOWN'],
  ['里', 'I-TOWN'],
  ['东', 'B-ROAD'],
  ['路', 'I-ROAD'],


In [40]:
gold = open('AL/dev.out', "r", encoding='UTF-8')
prediction = open('AL/p3.dev.out', "r", encoding='UTF-8')

#column separator
separator = ' '

#the column index for tags
outputColumnIndex = 1
#Read Gold data
observed = get_observed(gold)

#Read Predction data
predicted = get_predicted(prediction)

#Compare
compare_observed_to_predicted(observed, predicted)


#Entity in gold data: 8408
#Entity in prediction: 8496

#Correct Entity : 6740
Entity  precision: 0.7933
Entity  recall: 0.8016
Entity  F: 0.7974

#Correct Sentiment : 6088
Sentiment  precision: 0.7166
Sentiment  recall: 0.7241
Sentiment  F: 0.7203


# CN

In [41]:
cn_states = get_y_to_y("CN/train")
cn_y_to_y , cn_label_count_with_ss= get_y_to_y_dictionary(cn_states)
print(cn_y_to_y)
print(cn_label_count_with_ss)

{'START O': 3018, 'O O': 133402, 'O B-neutral': 5118, 'B-neutral I-neutral': 3300, 'I-neutral O': 3055, 'B-neutral O': 2755, 'O STOP': 4314, 'STOP START': 4500, 'I-neutral I-neutral': 3954, 'O B-positive': 2943, 'B-positive O': 1452, 'B-positive I-positive': 2160, 'I-positive O': 2034, 'B-positive STOP': 17, 'START B-positive': 592, 'I-positive I-positive': 2367, 'START B-neutral': 821, 'I-neutral B-neutral': 153, 'B-neutral B-neutral': 104, 'START B-negative': 70, 'B-negative O': 332, 'O B-negative': 449, 'I-positive B-neutral': 27, 'B-neutral STOP': 55, 'I-positive B-positive': 69, 'B-negative I-negative': 189, 'I-negative I-negative': 128, 'I-negative O': 178, 'I-neutral STOP': 75, 'B-negative B-negative': 6, 'I-neutral B-positive': 15, 'I-negative B-neutral': 2, 'B-negative STOP': 3, 'I-positive STOP': 30, 'I-negative B-negative': 2, 'B-positive B-positive': 26, 'B-positive B-neutral': 8, 'I-negative STOP': 7, 'B-neutral B-positive': 18, 'B-negative B-neutral': 1, 'I-neutral B-nega

In [42]:
try:
    f = open("CN/dev.in",encoding = 'utf-8')
    viterbi_cn = f.readlines()
finally:
    f.close()
    
cn_sentences = []
temp = []
for string in range(len(viterbi_cn)):
    if viterbi_cn[string] == '\n':
        cn_sentences.append(temp)
        temp = []
        continue
    viterbi_cn[string] = viterbi_cn[string].rstrip()
    temp.append(viterbi_cn[string]) 
    
print(cn_sentences[:2])

[['一', '觉醒', '来天', '都', '黑', '了', '。', '梦到', '了', '继科', '哥哥', '，', '给', '他', '做饭', '忙', '得', '团团转', '，', '继科', '哥哥', '很乖', '，', '不怎么', '爱', '说话', '。'], ['#', '向', '全世界', '吃货', '安利', '#', '哑', '壬', '迄', '听到', '看', '完', '就', '怀孕', '了', '的', '演唱', '，', '就', '觉得', '心情', '会', '好', '很', '[', '泪', ']', '[', '围脖', ']', '[', '手套', ']', '[', '生病', ']', '多', '的', '。', '眶', '贷']]


In [43]:
decode_viterbi(cn_sentences,smoothed_cn_word_count,smoothed_cn_label_count,cn_y_to_y,smoothed_cn_y_to_x,cn_label_count_with_ss,'CN/p3.dev.out')


100%|██████████| 642/642 [00:07<00:00, 86.69it/s] 


[[['一', 'O'],
  ['觉醒', 'O'],
  ['来天', 'O'],
  ['都', 'O'],
  ['黑', 'O'],
  ['了', 'O'],
  ['。', 'O'],
  ['梦到', 'O'],
  ['了', 'O'],
  ['继科', 'O'],
  ['哥哥', 'O'],
  ['，', 'O'],
  ['给', 'O'],
  ['他', 'O'],
  ['做饭', 'O'],
  ['忙', 'O'],
  ['得', 'O'],
  ['团团转', 'O'],
  ['，', 'O'],
  ['继科', 'O'],
  ['哥哥', 'O'],
  ['很乖', 'O'],
  ['，', 'O'],
  ['不怎么', 'O'],
  ['爱', 'O'],
  ['说话', 'O'],
  ['。', 'O']],
 [['#', 'O'],
  ['向', 'O'],
  ['全世界', 'O'],
  ['吃货', 'O'],
  ['安利', 'O'],
  ['#', 'O'],
  ['哑', 'O'],
  ['壬', 'O'],
  ['迄', 'O'],
  ['听到', 'O'],
  ['看', 'O'],
  ['完', 'O'],
  ['就', 'O'],
  ['怀孕', 'O'],
  ['了', 'O'],
  ['的', 'O'],
  ['演唱', 'O'],
  ['，', 'O'],
  ['就', 'O'],
  ['觉得', 'O'],
  ['心情', 'O'],
  ['会', 'O'],
  ['好', 'O'],
  ['很', 'O'],
  ['[', 'O'],
  ['泪', 'O'],
  [']', 'O'],
  ['[', 'O'],
  ['围脖', 'O'],
  [']', 'O'],
  ['[', 'O'],
  ['手套', 'O'],
  [']', 'O'],
  ['[', 'O'],
  ['生病', 'O'],
  [']', 'O'],
  ['多', 'O'],
  ['的', 'O'],
  ['。', 'O'],
  ['眶', 'O'],
  ['贷', 'O']],
 [['专访', 'O'],
  ['小

In [44]:
gold = open('CN/dev.out', "r", encoding='UTF-8')
prediction = open('CN/p3.dev.out', "r", encoding='UTF-8')

#column separator
separator = ' '

#the column index for tags
outputColumnIndex = 1
#Read Gold data
observed = get_observed(gold)

#Read Predction data
predicted = get_predicted(prediction)

#Compare
compare_observed_to_predicted(observed, predicted)


#Entity in gold data: 1478
#Entity in prediction: 712

#Correct Entity : 307
Entity  precision: 0.4312
Entity  recall: 0.2077
Entity  F: 0.2804

#Correct Sentiment : 210
Sentiment  precision: 0.2949
Sentiment  recall: 0.1421
Sentiment  F: 0.1918


## SG

In [45]:
sg_states = get_y_to_y("SG/train")
sg_y_to_y , sg_label_count_with_ss= get_y_to_y_dictionary(sg_states)

In [46]:
print(sg_y_to_y)

{'START O': 19007, 'O O': 230383, 'O B-positive': 6461, 'B-positive I-positive': 3083, 'I-positive O': 2969, 'O STOP': 20667, 'STOP START': 21750, 'O B-neutral': 18551, 'B-neutral O': 10011, 'B-neutral I-neutral': 9531, 'I-neutral I-neutral': 9362, 'I-neutral O': 9243, 'O B-negative': 3348, 'B-negative O': 2635, 'START B-positive': 914, 'B-positive O': 4107, 'B-positive STOP': 211, 'START B-neutral': 1339, 'START B-negative': 491, 'B-negative I-negative': 1099, 'I-negative O': 1055, 'I-negative I-negative': 410, 'B-neutral STOP': 406, 'I-positive I-positive': 1816, 'B-negative STOP': 105, 'I-positive B-neutral': 5, 'B-neutral B-neutral': 214, 'B-positive B-positive': 40, 'I-positive STOP': 100, 'I-neutral STOP': 223, 'I-neutral B-neutral': 55, 'I-negative STOP': 39, 'B-neutral B-positive': 23, 'I-positive B-positive': 9, 'B-neutral B-negative': 5, 'I-neutral B-positive': 9, 'I-negative B-neutral': 2, 'B-negative B-negative': 16, 'B-negative B-neutral': 9, 'B-positive B-neutral': 15, 'I

In [47]:
try:
    f = open("SG/dev.in",encoding = 'utf-8')
    viterbi_sg = f.readlines()
finally:
    f.close()
    
sg_sentences = []
temp = []
for string in range(len(viterbi_sg)):
    if viterbi_sg[string] == '\n':
        sg_sentences.append(temp)
        temp = []
        continue
    viterbi_sg[string] = viterbi_sg[string].rstrip()
    temp.append(viterbi_sg[string]) 
    
print(sg_sentences[:2])

[['Tour', 'Scotland', 'followers', 'to', 'visit', '@beley_crysta2', ',', '@MyExpatJob', ',', ',', '@paridise15', ',', '@JCBlakeney76', ',', '@UnwearyWorld', ',', '@szilviade', ',', '@garrywatts1231'], ['Overwatch', ':', 'tip', '!', 'Roadhog', 'is', 'fat', 'so', "he's", 'easier', 'to', 'hit', '!', 'Me', ':', 'wtf', 'blizzard']]


In [48]:
decode_viterbi(sg_sentences,smoothed_sg_word_count,smoothed_sg_label_count,sg_y_to_y,smoothed_sg_y_to_x,sg_label_count_with_ss,'SG/p3.dev.out')


100%|██████████| 3107/3107 [00:12<00:00, 257.36it/s]


[[['Tour', 'O'],
  ['Scotland', 'B-neutral'],
  ['followers', 'O'],
  ['to', 'O'],
  ['visit', 'O'],
  ['@beley_crysta2', 'O'],
  [',', 'O'],
  ['@MyExpatJob', 'O'],
  [',', 'O'],
  [',', 'O'],
  ['@paridise15', 'O'],
  [',', 'O'],
  ['@JCBlakeney76', 'O'],
  [',', 'O'],
  ['@UnwearyWorld', 'O'],
  [',', 'O'],
  ['@szilviade', 'O'],
  [',', 'O'],
  ['@garrywatts1231', 'O']],
 [['Overwatch', 'B-positive'],
  [':', 'O'],
  ['tip', 'O'],
  ['!', 'O'],
  ['Roadhog', 'O'],
  ['is', 'O'],
  ['fat', 'O'],
  ['so', 'O'],
  ["he's", 'O'],
  ['easier', 'O'],
  ['to', 'O'],
  ['hit', 'O'],
  ['!', 'O'],
  ['Me', 'O'],
  [':', 'O'],
  ['wtf', 'O'],
  ['blizzard', 'O']],
 [["I'm", 'O'],
  ['at', 'O'],
  ['Club', 'B-neutral'],
  ['Tryst', 'I-neutral'],
  ['in', 'I-neutral'],
  ['Singapore', 'I-neutral'],
  ['https://t.co/imMAYtNBjH', 'O']],
 [['@alexiadavis__', 'O'],
  ['lol', 'O'],
  ["don't", 'O'],
  ['start', 'O'],
  ['this', 'O'],
  ['Alexia', 'O']],
 [['Fuck', 'O'],
  ['A', 'O'],
  ['Release', 

In [49]:
gold = open('SG/dev.out', "r", encoding='UTF-8')
prediction = open('SG/p3.dev.out', "r", encoding='UTF-8')

#column separator
separator = ' '

#the column index for tags
outputColumnIndex = 1
#Read Gold data
observed = get_observed(gold)

#Read Predction data
predicted = get_predicted(prediction)

#Compare
compare_observed_to_predicted(observed, predicted)


#Entity in gold data: 4537
#Entity in prediction: 3005

#Correct Entity : 1663
Entity  precision: 0.5534
Entity  recall: 0.3665
Entity  F: 0.4410

#Correct Sentiment : 1036
Sentiment  precision: 0.3448
Sentiment  recall: 0.2283
Sentiment  F: 0.2747


In [50]:
# test np argsort

# np.argsort([10,8,15,123,125,123,5121,312, 11],-7)[-7:]
array = [10,8,15,123,125,123,5121,312, 11]
idx = np.argsort([10,8,15,123,125,123,5121,312, 11])[-7:]
print(idx)
print(array[idx[0]])

import math

[8 2 3 5 4 7 6]
11


## Part 4

In [51]:
def viterbi_7(sentence, word_dict,label_dict,yy_dict,yx_dict,label_dict_with_ss):
    result = []
    node_matrix = []
    backpointers = []
    calc_copy = sentence.copy()
    for word in range(len(sentence)):
         if calc_copy[word] not in word_dict:
                calc_copy[word] = '#UNK#'
                
    for word in range(len(calc_copy)): 
        
        if word==0:
            temp = []
            for label in list(label_dict.keys()):
                emission = get_emission(calc_copy[word],label,yx_dict,label_dict)
                if emission != 0:
                    emission = math.log(emission)
                else:
                    emission = -999999999
                transmission = get_transmission('START',label,yy_dict,label_dict_with_ss)
                if transmission != 0:
                    transmission = math.log(transmission)
                else:
                    transmission = -999999999
                node_value = emission + transmission
                temp.append(node_value)
            node_matrix.append(temp)
            continue
            
            
        storage = []   
        pointer_7 = []
        if word == 1:
            for label in list(label_dict.keys()):
                find_max_list = []
                node_7 = []
                for node in range(len(list(label_dict.keys()))): ## node in node_matrix (previously) 
                    prev_node = node_matrix[word-1][node]
                    emission = get_emission(calc_copy[word],label,yx_dict,label_dict)
                    transmission = get_transmission(list(label_dict.keys())[node],label,yy_dict,label_dict_with_ss)
                    if emission != 0:
                        emission = math.log(emission)
                    else:
                        emission = -999999999
                    if transmission != 0:
                        transmission = math.log(transmission)
                    else:
                        transmission = -999999999

                    node_value = prev_node+emission+transmission
                    find_max_list.append(node_value)

                indices = np.argsort(find_max_list)[-7:]  # returns a list of indexes from in ascending order, #the first element is the 7th sequence
                for ind in indices:
                    node_7.append(find_max_list[ind]) # adds the top 7 lists inside in ascending order
                storage.append(node_7)
                pointer_7.append(indices)
            backpointers.append(pointer_7)
            node_matrix.append(storage)
            continue
            
            
        storage = []   
        pointer_7 = []
        for label in list(label_dict.keys()):
            node_7 = []
            find_max_list = []
            for node in range(len(list(label_dict.keys()))): ## node in node_matrix (previously)
                max_per_node = []
                for top_7 in range(len(node_matrix[word-1][node])):
                    prev_node = node_matrix[word-1][node][top_7]
                    emission = get_emission(calc_copy[word],label,yx_dict,label_dict)
                    transmission = get_transmission(list(label_dict.keys())[node],label,yy_dict,label_dict_with_ss)
                    if emission != 0:
                        emission = math.log(emission)
                    else:
                        emission = -999999999
                    if transmission != 0:
                        transmission = math.log(transmission)
                    else:
                        transmission = -999999999

                    node_value = prev_node+emission+transmission
                    max_per_node.append(node_value)
                index = np.argmax(max_per_node)
                find_max_list.append(max_per_node[index])
            
            indices = np.argsort(find_max_list)[-7:]
            for ind in indices:
                node_7.append(find_max_list[ind])
            storage.append(node_7)
            pointer_7.append(indices)
        backpointers.append(pointer_7)
        node_matrix.append(storage) 
        
    # STOP NODE
    find_max_stop = []
    node_7 = []
    for node in range(len(list(label_dict.keys()))): ## node in node_matrix
        max_per_node = []
        for top_7 in range(len(node_matrix[len(sentence)-1][node])):
            prev_node = node_matrix[len(sentence)-1][node][top_7]
            transmission = get_transmission(list(label_dict.keys())[node],label,yy_dict,label_dict_with_ss)
            if transmission != 0:
                transmission = math.log(transmission)
            else:
                transmission = -999999999
            node_value = prev_node+transmission
            max_per_node.append(node_value)
            
        index = np.argmax(max_per_node)
        find_max_stop.append(max_per_node[index])
    indices = np.argsort(find_max_stop)[-7:]
    for ind in indices:
        node_7.append(find_max_stop[ind])
#     storage.append(node_7)
#     pointer_7.append(indices)
    backpointers.append(indices)
    node_matrix.append(find_max_stop) 
        

#     print(len(node_matrix))
#     print(len(node_matrix[-1]))   
#     print(node_matrix[-1])
#     print(len(backpointers[2]))
#     print(backpointers[2])
#     print(node_matrix[0])
    return node_matrix[::-1], backpointers[::-1]

trynode, tryback =viterbi_7(en_sentences[0],smoothed_en_word_count,smoothed_en_label_count,en_y_to_y,smoothed_en_y_to_x,en_label_count_with_ss)

In [52]:
def get_index_from_viterbi_7(node_matrix,backpointers):
    ## starting from stop
    indexes = []
    for pointer_list in range(len(backpointers)):
        if pointer_list == 0:
            indexes.append(backpointers[pointer_list][0])# returns 7th
            continue
        backtrack_index = indexes[pointer_list-1]
        indexes.append(backpointers[pointer_list][backtrack_index][6]) ## 0 returns the best
    return indexes[::-1]

# get_index_from_viterbi_7(trynode,tryback)

In [53]:
def decode_7th(sentences, word_dict,label_dict,yy_dict,yx_dict,label_dict_with_ss,filename):
    results = []
    file = open(filename,'w',encoding = 'utf-8')
    for sentence in tqdm(range(len(sentences))):
        sentence_result = []
        inverted_node_matrix , inverted_back_pointers = viterbi_7(sentences[sentence],word_dict,label_dict,yy_dict,yx_dict,label_dict_with_ss)
        prediction_indexes = get_index_from_viterbi_7(inverted_node_matrix,inverted_back_pointers)
        for word in range(len(sentences[sentence])):
            temp = []
            temp.append(sentences[sentence][word])
            temp.append(list(label_dict.keys())[prediction_indexes[word]])
            sentence_result.append(temp)
        results.append(sentence_result)

    for sentence in results:
        for tup in sentence:
            file.write(tup[0]+ ' ' + tup[1]+'\n')
        file.write('\n')
    
    file.close()
    return results

## EN

In [54]:
decode_7th(en_sentences,smoothed_en_word_count,smoothed_en_label_count,en_y_to_y,smoothed_en_y_to_x,en_label_count_with_ss,'EN/p4.dev.out')


100%|██████████| 1094/1094 [05:42<00:00,  3.19it/s]


[[['HBO', 'B-NP'],
  ['has', 'B-VP'],
  ['close', 'I-VP'],
  ['to', 'B-PP'],
  ['24', 'B-NP'],
  ['million', 'I-NP'],
  ['subscribers', 'I-NP'],
  ['to', 'B-PP'],
  ['its', 'B-NP'],
  ['HBO', 'I-NP'],
  ['and', 'O'],
  ['Cinemax', 'B-NP'],
  ['networks', 'I-NP'],
  [',', 'O'],
  ['while', 'B-SBAR'],
  ['Showtime', 'B-NP'],
  ['and', 'O'],
  ['its', 'B-NP'],
  ['sister', 'I-NP'],
  ['service', 'I-NP'],
  [',', 'O'],
  ['The', 'B-NP'],
  ['Movie', 'I-NP'],
  ['Channel', 'I-NP'],
  [',', 'O'],
  ['have', 'B-VP'],
  ['only', 'I-VP'],
  ['about', 'B-PP'],
  ['10', 'B-NP'],
  ['million', 'I-NP'],
  [',', 'O'],
  ['according', 'B-PP'],
  ['to', 'B-PP'],
  ['Paul', 'B-NP'],
  ['Kagan', 'I-NP'],
  ['Associates', 'I-NP'],
  [',', 'O'],
  ['a', 'B-NP'],
  ['Carmel', 'I-NP'],
  [',', 'O'],
  ['Calif.', 'B-NP'],
  [',', 'O'],
  ['research', 'B-NP'],
  ['firm', 'I-NP'],
  ['.', 'B-ADVP']],
 [['WASHINGTON', 'B-NP'],
  ['LIES', 'I-NP'],
  ['LOW', 'I-NP'],
  ['after', 'B-PP'],
  ['the', 'B-NP'],
  ['st

In [55]:
gold = open('EN/dev.out', "r", encoding='UTF-8')
prediction = open('EN/p4.dev.out', "r", encoding='UTF-8')

#column separator
separator = ' '

#the column index for tags
outputColumnIndex = 1
#Read Gold data
observed = get_observed(gold)

#Read Predction data
predicted = get_predicted(prediction)

#Compare
compare_observed_to_predicted(observed, predicted)


#Entity in gold data: 13179
#Entity in prediction: 14144

#Correct Entity : 10920
Entity  precision: 0.7721
Entity  recall: 0.8286
Entity  F: 0.7993

#Correct Sentiment : 10500
Sentiment  precision: 0.7424
Sentiment  recall: 0.7967
Sentiment  F: 0.7686


## AL

In [56]:
decode_7th(al_sentences,smoothed_al_word_count,smoothed_al_label_count,al_y_to_y,smoothed_al_y_to_x,al_label_count_with_ss,'AL/p4.dev.out')


100%|██████████| 1492/1492 [19:31<00:00,  1.27it/s]


[[['杭', 'B-CITY'],
  ['州', 'I-CITY'],
  ['市', 'I-CITY'],
  ['西', 'B-DISTRICT'],
  ['湖', 'I-DISTRICT'],
  ['区', 'I-DISTRICT'],
  ['古', 'B-TOWN'],
  ['荡', 'I-TOWN'],
  ['新', 'B-COMMUNITY'],
  ['村', 'I-COMMUNITY'],
  ['西', 'I-COMMUNITY'],
  ['34', 'B-HOUSENO'],
  ['幢', 'I-HOUSENO'],
  ['八', 'B-CELLNO'],
  ['单', 'I-CELLNO'],
  ['元', 'I-CELLNO'],
  ['1375', 'B-POI']],
 [['塘', 'B-TOWN'],
  ['雅', 'I-TOWN'],
  ['镇', 'I-TOWN'],
  ['顶', 'B-POI'],
  ['塘', 'I-POI'],
  ['工', 'I-POI'],
  ['业', 'I-POI'],
  ['园', 'I-POI'],
  ['鑫', 'I-POI'],
  ['龙', 'I-POI'],
  ['水', 'I-POI'],
  ['准', 'I-POI'],
  ['仪', 'I-POI'],
  ['器', 'I-POI'],
  ['有', 'I-POI'],
  ['限', 'I-POI'],
  ['公', 'I-POI'],
  ['司', 'B-TOWN']],
 [['中', 'B-COUNTRY'],
  ['国', 'I-COUNTRY'],
  ['浙', 'B-PROV'],
  ['江', 'I-PROV'],
  ['省', 'I-PROV'],
  ['温', 'B-CITY'],
  ['州', 'I-CITY'],
  ['市', 'I-CITY'],
  ['鹿', 'B-DISTRICT'],
  ['城', 'I-DISTRICT'],
  ['区', 'I-DISTRICT'],
  ['百', 'B-TOWN'],
  ['里', 'I-TOWN'],
  ['东', 'B-ROAD'],
  ['路', 'I-ROAD'],
  

In [57]:
gold = open('AL/dev.out', "r", encoding='UTF-8')
prediction = open('AL/p4.dev.out', "r", encoding='UTF-8')

#column separator
separator = ' '

#the column index for tags
outputColumnIndex = 1
#Read Gold data
observed = get_observed(gold)

#Read Predction data
predicted = get_predicted(prediction)

#Compare
compare_observed_to_predicted(observed, predicted)


#Entity in gold data: 8408
#Entity in prediction: 8922

#Correct Entity : 6088
Entity  precision: 0.6824
Entity  recall: 0.7241
Entity  F: 0.7026

#Correct Sentiment : 4939
Sentiment  precision: 0.5536
Sentiment  recall: 0.5874
Sentiment  F: 0.5700
